In [1]:
import pandas as pd
import numpy as np

## Cleaning the target variable
* Removing observations that can't be used 
    - Loans 
    - Free transfers 
    - Academy promotions
* Converting the fee to an integer
     - Stripping the currency symbol
     - Converting string decimal notation to a multiplier
     - Converting fee to integer on same scale

In [2]:
tf_df = pd.read_csv('data/Top_8_leagues_past_6_windows.csv')

In [3]:
tf_df.drop(labels="Unnamed: 0", axis=1, inplace=True)

In [4]:
tf_df.head()

player  age nationality            position  \
0   Ante Palaversa   18     Croatia  Defensive Midfield   
1       Ko Itakura   21       Japan         Centre-Back   
2   Yangel Herrera   20   Venezuela    Central Midfield   
3    Marlos Moreno   22    Colombia        Right Winger   
4  Anthony Cáceres   26   Australia    Central Midfield   

                   selling_club previous_league est_market_value  \
0              HNK Hajduk Split         Croatia          £495Th.   
1             Kawasaki Frontale           Japan          £630Th.   
2              New York City FC   United States          £900Th.   
3  Clube de Regatas do Flamengo          Brazil          £450Th.   
4             Melbourne City FC       Australia          £450Th.   

                       fee      buying_club window  year buying_league  
0                   £5.67m  Manchester City  s_w=w  2018           GB1  
1                  £990Th.  Manchester City  s_w=w  2018           GB1  
2  End of loanDec 31, 2018  Manchester City  s_w=w  2018           GB1  
3  End of loanDec 31, 2018  Manchester City  s_w=w  2018           GB1  
4  End of loanDec 31, 2018  Manchester City  s_w=w  2018           GB1

In [5]:
# Multiple players have duplicate entries e.g., Nikola Kalinic 2020, Wesley Fofana 2020, Moussa Konaté 2020
# tf_df.loc[tf_df['player']=='Nikola Kalinic',:]

In [6]:
tf_df.shape

(9666, 12)

In [7]:
# Not unusual for players to be transfered multiple times even in same year so only removing duplicates with the
# exact same fee, buying club and selling club in the same year.
tf_df.drop_duplicates(subset=['player','selling_club','buying_club','fee','year'], keep='first', inplace=True)

In [8]:
tf_df.shape

(9378, 12)

In [9]:
tf_df['fee'].value_counts()

free transfer              1139
loan transfer              1088
-                          1010
End of loanJun 30, 2019     988
End of loanJun 30, 2018     932
                           ... 
£78.30m                       1
End of loanNov 30, 2018       1
£432Th.                       1
End of loanAug 21, 2019       1
End of loanJan 20, 2019       1
Name: fee, Length: 627, dtype: int64

### Counting and labeling loan deals

In [10]:
tf_df['loan'] = tf_df['fee'].apply(lambda x: 1 if 'loan' in x.lower() else 0)

In [11]:
tf_df['loan'].value_counts()

1    5056
0    4322
Name: loan, dtype: int64

5056 loan deals.  Not unexpected.

### Counting and labeling free transfers 

In [12]:
tf_df['free'] = tf_df['fee'].apply(lambda x: 1 if 'free' in x.lower() else 0)

In [13]:
tf_df['free'].value_counts()

0    8239
1    1139
Name: free, dtype: int64

In [14]:
#Want to see if there are any other types of free transfers
# pd.options.display.max_rows = 1200
tf_df.loc[tf_df['free'] == 1, 'fee']

20      free transfer
33      free transfer
46      free transfer
86      free transfer
131     free transfer
            ...      
9636    free transfer
9637    free transfer
9638    free transfer
9652    free transfer
9653    free transfer
Name: fee, Length: 1139, dtype: object

Free transfers happen when a contract is run down; contract length is an important determinant of transfer fee but I don't have that information.  Here, while it would be important for clubs to know how much time is left on a contract (as they may be able to use that as leverage to get a better deal) I'll use the model to bench mark the going market rate for a player of that profile.

### In the fee value count: 1010 "-"
### These appear to be internal promotions, e.g., from the U23 team. Investigating and labeling here

In [15]:
# pd.options.display.max_rows = 30
tf_df.loc[tf_df['fee'] == "-", ['player','fee','selling_club','buying_club']]

player fee          selling_club       buying_club
16     Callum Hudson-Odoi   -        Chelsea FC U23        Chelsea FC
19          Eddie Nketiah   -        Arsenal FC U23        Arsenal FC
29         Sean Longstaff   -  Newcastle United U23  Newcastle United
42            Kyle Taylor   -   AFC Bournemouth U21   AFC Bournemouth
44            Samir Nasri   -      Disqualification   West Ham United
...                   ...  ..                   ...               ...
9591       Andrey Bokovoy   -           FK Sochi II          FC Sochi
9603         Arsen Adamov   -      Akhmat Grozny II     Akhmat Grozny
9621  Vladimir Kabakhidze   -          FK Tambov II       PFK  Tambov
9639         Nikita Repin   -     Rotor 2 Volgograd   Rotor Volgograd
9646     Nikita Muromskiy   -     Rotor 2 Volgograd   Rotor Volgograd

[1010 rows x 4 columns]

The fee "-" are internal promotions or picking up players without a club for free.  Will not be used in our model

In [16]:
# removing loans, free transfers, academy promotions
tfdf2 = tf_df.loc[(tf_df['fee'] != "-")&(tf_df['loan'] == 0)&(tf_df['free'] == 0), :]

In [17]:
tfdf2.head()

player  age    nationality            position  \
0      Ante Palaversa   18        Croatia  Defensive Midfield   
1          Ko Itakura   21          Japan         Centre-Back   
10  Christian Pulisic   20  United States         Left Winger   
27     Miguel Almirón   24       Paraguay  Attacking Midfield   
38    Dominic Solanke   21        England      Centre-Forward   

         selling_club previous_league est_market_value      fee  \
0    HNK Hajduk Split         Croatia          £495Th.   £5.67m   
1   Kawasaki Frontale           Japan          £630Th.  £990Th.   
10  Borussia Dortmund         Germany          £45.00m  £57.60m   
27  Atlanta United FC   United States          £13.50m  £21.60m   
38       Liverpool FC         England           £9.00m  £19.08m   

         buying_club window  year buying_league  loan  free  
0    Manchester City  s_w=w  2018           GB1     0     0  
1    Manchester City  s_w=w  2018           GB1     0     0  
10        Chelsea FC  s_w=w  2018           GB1     0     0  
27  Newcastle United  s_w=w  2018           GB1     0     0  
38   AFC Bournemouth  s_w=w  2018           GB1     0     0

In [18]:
tfdf2.shape

(2173, 14)

In [19]:
# pd.options.display.max_rows = 20
# tfdf2['previous_league'].value_counts()
# Top 6 countries:
# Italy                   299
# France                  258
# England                 225
# Spain                   222
# Portugal                175
# Germany                 172

Evaluating the value counts of previous league - there are only 1176 observations where a player was bought from a league in the Big 5.  Currently only have detailed statistical profile of players from the top 5 leagues.  Looked to pull in more years and data from more leagues but fbref doesn't have detailed stats for leagues outside the top 5 (except for MLS) or for more than 3 years.  Will have to proceed with what I have understanding this is a bit reduced in scope by virture of data.

In [20]:
#Creating an indicator for bought from a top five league to faciliate merging with statistical data
tfdf2['buying_top_5'] = tfdf2['previous_league'].map(lambda x: 1 if x in ["Italy",'France','England','Spain','Germany'] else 0)

/Users/ericroberts/anaconda3/envs/learn-env/lib/python3.6/site-packages/ipykernel_launcher.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


In [21]:
pd.options.mode.chained_assignment = None  # default='warn'

In [22]:
tfdf2['buying_top_5'].value_counts()

1    1176
0     997
Name: buying_top_5, dtype: int64

In [23]:
tfdf3 = tfdf2.loc[(tfdf2['buying_top_5'] == 1), :]

In [24]:
tfdf3.shape

(1176, 15)

### Turning fee column into an integer

In [25]:
tfdf3['fee'].value_counts()

?          69
£1.80m     65
£2.70m     45
£900Th.    42
£3.60m     41
           ..
£30.06m     1
£35.28m     1
£248Th.     1
£20.16m     1
£4.77m      1
Name: fee, Length: 265, dtype: int64

In [26]:
filt =  tfdf3['fee']=='?'
tfdf3.drop(index=tfdf3[filt].index, inplace=True)

In [27]:
tfdf3['fee'].value_counts()

£1.80m     65
£2.70m     45
£900Th.    42
£4.50m     41
£3.60m     41
           ..
£30.06m     1
£35.28m     1
£248Th.     1
£20.16m     1
£4.77m      1
Name: fee, Length: 264, dtype: int64

In [28]:
tfdf3['currency'] = tfdf3['fee'].apply(lambda x: x[0])

In [29]:
tfdf3['currency'].value_counts()

£    1107
Name: currency, dtype: int64

In [30]:
tfdf3['multiplier'] = tfdf3['fee'].str.extract(r'([a-zA-Z]+)')
                                                                         

In [31]:
tfdf3['multiplier'].value_counts()

m     936
Th    168
Name: multiplier, dtype: int64

In [32]:
tfdf3.isna().sum()

player              0
age                 0
nationality         0
position            0
selling_club        0
previous_league     0
est_market_value    0
fee                 0
buying_club         0
window              0
year                0
buying_league       0
loan                0
free                0
buying_top_5        0
currency            0
multiplier          3
dtype: int64

In [33]:
# If there was no multiplier specified assuming it is in the specified units
tfdf3.fillna(value=1, inplace=True)

In [34]:
tfdf3['multiplier'].value_counts()

m     936
Th    168
1       3
Name: multiplier, dtype: int64

In [35]:
tfdf3['fee_numerical'] = tfdf3['fee'].str.extract(r'([0-9]+\.?[0-9]+)')

In [36]:
# convert numeric columns to appropiate dypes
tfdf3 = tfdf3.astype({'fee_numerical':'float'})

In [37]:
tfdf3.loc[tfdf3['multiplier'] == 'm', 'mult_num'] = 1000000
tfdf3.loc[tfdf3['multiplier'] == 'Th', 'mult_num'] = 1000
tfdf3.loc[tfdf3['multiplier'] == 1, 'mult_num'] = 1

In [38]:
tfdf3['fee_final'] = tfdf3['fee_numerical']*tfdf3['mult_num']

In [39]:
tfdf3['fee_final']

10      57600000.0
38      19080000.0
39      12240000.0
57       1530000.0
65      18900000.0
           ...    
9232     2700000.0
9320    18000000.0
9321     5400000.0
9455    10800000.0
9466     4950000.0
Name: fee_final, Length: 1107, dtype: float64

In [ ]:
# tfdf3.head()

## Creating variables to index on for merging:
Need to assess and clean variables for this purpose in both dataframes:
* Player name
* Year of stats/year of transfer - using a one year lag (e.g., purchase in 2018 will be modeled with 2017 stats.
    - Note: the winter transfer window is labeled a year early (winter 2018 was the Jan 2019 window). Therefore use the 2017/2018 stats to predict winter/summer 2018 prices
* Columns with same information but different format:
    * club name in stats/selling club in transfers
    * nationality
    * previous_league/league
    * position

In [40]:
statsdf = pd.read_csv('data/Player_stats_top_5_leagues_2017_to_2020.csv')

In [ ]:
# tfdf3.head()

In [ ]:
# tfdf3['player'].value_counts()

In [ ]:
# tfdf3.loc[tfdf3['player']=='Enric Gallego',:]

In [ ]:
# statsdf.loc[statsdf['players']=='Enric Gallego',:]

In [ ]:
# statsdf.head()

## ASSESSING MISSINGNESS

In [41]:
tfdf3.isna().sum()

player              0
age                 0
nationality         0
position            0
selling_club        0
previous_league     0
est_market_value    0
fee                 0
buying_club         0
window              0
year                0
buying_league       0
loan                0
free                0
buying_top_5        0
currency            0
multiplier          0
fee_numerical       0
mult_num            0
fee_final           0
dtype: int64

In [42]:
pd.options.display.max_rows = 140
statsdf.isna().sum()

players                          0
nationality                      1
team                             0
position                         1
age                              7
birth_year                       7
games                            0
games_start                      0
mins                             0
goals                            0
assists                          0
pens_successful                  0
pens_attempts                    0
yellow_cards                     0
red_cards                        0
goals_per_90                     0
assists_per_90                   0
goals_and_assists_per_90         0
goals_pk_per_90                  0
goals_assists_pk_per_90          0
xg                              10
npxp                            10
xa                              10
xg_per90                        20
xa_per90                        20
xg_xa_per90_list                20
npxg_per90_list                 20
npxg_xa_per90                   20
full_90s_played     

* variables that can be calculated:
    - 'aerials_won_pct', 'shots_on_target_pct', 'goals_per_shot', 'goals_per_shot_on_target', 'avg_shot_dist', 'npxg_per_shot', 'pass_percent', 'pass_percent_short', 'pass_percent_medium', 'pass_percent_long', 'dribble_tackles_pct', 'pressure_regain_pct', 'dribbles_completed_pct', 'passes_received_pct'
* variables to use fillna:
    - progressive_passes

In [43]:
#Following variables are missing hundreds of observations or are duplicates between scraped pages
# Dropping columns
statsdf.drop(labels=['aerials_won_pct', 'shots_on_target_pct','goals_per_shot','goals_per_shot_on_target',
                    'avg_shot_dist','npxg_per_shot','pass_percent','pass_percent_short','pass_percent_medium',
                    'pass_percent_long','dribble_tackles_pct','pressure_regain_pct','dribbles_completed_pct', 
                    'passes_received_pct','goals.1','pens_successful.1','pens_attempts.1','xg.1',
                    'full_90s_played.1','assists.1','xa.1','full_90s_played.2'], axis=1, inplace=True)

In [44]:
#Assessing remaining missing variables 
pd.options.display.max_rows = 140
statsdf.isna().sum()

players                        0
nationality                    1
team                           0
position                       1
age                            7
birth_year                     7
games                          0
games_start                    0
mins                           0
goals                          0
assists                        0
pens_successful                0
pens_attempts                  0
yellow_cards                   0
red_cards                      0
goals_per_90                   0
assists_per_90                 0
goals_and_assists_per_90       0
goals_pk_per_90                0
goals_assists_pk_per_90        0
xg                            10
npxp                          10
xa                            10
xg_per90                      20
xa_per90                      20
xg_xa_per90_list              20
npxg_per90_list               20
npxg_xa_per90                 20
full_90s_played                0
shots_total                    7
shots_on_t

In [45]:
statsdf2 = statsdf.fillna(value='?')

In [46]:
# Lots of variables are missing 10 or 20 observations.  Guessing these are all on the same player,
# likely with few appearances and therefore no statistics to report.  Confirming here.
pd.options.display.max_columns = 116
statsdf2.loc[statsdf2['xg_per90'] == '?',:]

players nationality            team position age  \
1685         Vincent Janssen      nl NED       Tottenham       DF  23   
1808  Georges-Kévin N'Koudou      fr FRA       Tottenham       MF  22   
1821           Aiden O'Neill      au AUS         Burnley       MF  19   
1937           Axel Tuanzebe     eng ENG  Manchester Utd       FW  19   
3308              Kévin Zohi      ml MLI      Strasbourg       MF  20   
3344       Mariusz Stępiński      pl POL          Nantes       FW  22   
3446          Romain Perraud      fr FRA            Nice       MF  19   
3472            Sloan Privat      fr FRA        Guingamp       FW  28   
3559              Yusuf Sari      tr TUR       Marseille       FW  18   
3836       Christian Kouakou      ci CIV            Caen       FW  27   
4505         Ahmad Ngouyamsa      cm CMR           Dijon       DF  18   
4774       Christian Rutjens           ?       Benevento        ?   ?   
4832        Emanuele Torrasi      it ITA           Milan       MF  18   
4886    Gabriele Marchegiani      it ITA            SPAL       GK  21   
5025        Marco Tumminello      it ITA            Roma       FW  18   
5785          Álex Centelles      es ESP         Udinese       DF  20   
6431          Sergio Arribas      es ESP         Leganés       FW  22   
6760               Álex Mula      es ESP          Málaga    MF,FW  21   
6767       Fahad Al-Muwallad      sa KSA         Levante    FW,MF  20   
6948        Asier Villalibre      es ESP   Athletic Club       FW  19   

     birth_year  games  games_start mins  goals  assists  pens_successful  \
1685       1994      1            0    1      0        0                0   
1808       1995      1            0    1      0        0                0   
1821       1998      1            0    1      0        0                0   
1937       1997      1            0    1      0        0                0   
3308       1996      1            0    1      0        0                0   
3344       1995      1            0    1      0        0                0   
3446       1997      1            0    1      0        0                0   
3472       1989      1            0    1      0        0                0   
3559       1998      1            0    1      0        0                0   
3836       1991      1            0   13      0        0                0   
4505       2000      1            0   55      0        0                0   
4774          ?      1            0    1      0        0                0   
4832       1999      1            0    6      0        0                0   
4886       1996      1            0    1      0        0                0   
5025       1998      1            0    1      0        0                0   
5785       1997      8            6  583      0        0                0   
6431       1995      1            0   24      0        0                0   
6760       1996     11            7  560      0        0                0   
6767       1996      2            0   29      0        0                0   
6948       1997      1            1   90      0        0                0   

      pens_attempts  yellow_cards  red_cards  goals_per_90  assists_per_90  \
1685              0             0          0           0.0             0.0   
1808              0             0          0           0.0             0.0   
1821              0             0          0           0.0             0.0   
1937              0             0          0           0.0             0.0   
3308              0             0          0           0.0             0.0   
3344              0             0          0           0.0             0.0   
3446              0             0          0           0.0             0.0   
3472              0             0          0           0.0             0.0   
3559              0             0          0           0.0             0.0   
3836              0             0          0           0.0             0.0   
4505       

In [47]:
#Confirmed - of the players with missing values 17 have 1 appearance, one 2, one 8 and one 11 (the latter two 
#greater than 6 full 90's) going to zero fill
statsdf.fillna(value=0, inplace=True)

In [48]:
#Not sure why but Christian Rutjens (index=4774 has no information)
statsdf.drop(index=4774, inplace=True)

In [49]:
statsdf.isna().sum()

players                       0
nationality                   0
team                          0
position                      0
age                           0
birth_year                    0
games                         0
games_start                   0
mins                          0
goals                         0
assists                       0
pens_successful               0
pens_attempts                 0
yellow_cards                  0
red_cards                     0
goals_per_90                  0
assists_per_90                0
goals_and_assists_per_90      0
goals_pk_per_90               0
goals_assists_pk_per_90       0
xg                            0
npxp                          0
xa                            0
xg_per90                      0
xa_per90                      0
xg_xa_per90_list              0
npxg_per90_list               0
npxg_xa_per90                 0
full_90s_played               0
shots_total                   0
shots_on_target               0
shots_to

### Years
* Year of stats/year of transfer - using a one year lag (e.g., purchase in 2018 will be modeled with 2017 stats.
    - Note: the winter transfer window is labeled a year early (winter 2018 was the Jan 2019 window). Therefore use the 2017/2018 stats to predict winter/summer 2018 prices

In [50]:
print(tfdf3['year'].value_counts())
print(tfdf3['window'].value_counts())
print(statsdf['year'].value_counts())

2019    435
2018    401
2020    271
Name: year, dtype: int64
s_w=s    976
s_w=w    131
Name: window, dtype: int64
2019-2020    2732
2017-2018    2686
2018-2019    2658
Name: year, dtype: int64


In [51]:
# tfdf3.head(20)

In [52]:
tfdf3['index_year'] = tfdf3['year']

In [53]:
#renaming year as transfer year so that after merging the column is perserved 
#and interpretable
tfdf3.rename(columns={'year':'transfer_year'}, inplace=True)

In [54]:
#Select the first 4 digits (the first year) for the stats years
statsdf['index_year'] = statsdf['year'].apply(lambda x: x[0:4])

In [55]:
#convert to int
statsdf = statsdf.astype({'index_year':'int'})

In [56]:
#Adding 1 to faciliate matching of the lag
#index_year will now match up the transfer to the performance stats lagged by one year
statsdf['index_year'] = statsdf['index_year']+1

In [57]:
#renaming year as stats_year so that after merging the column is perserved 
#and interpretable
statsdf.rename(columns={'year':'stats_year'}, inplace=True)

In [58]:
statsdf['index_year'].value_counts()

2020    2732
2018    2686
2019    2658
Name: index_year, dtype: int64

### Player name

In [59]:
tfdf3['player'].nunique()

1024

In [60]:
statsdf['players'].value_counts()

Raúl García          8
Adama Traoré         6
Rafinha              6
Naldo                6
Marcelo              6
                    ..
Maxence Rivera       1
Francisco Montero    1
Hugo Magnetti        1
Ørjan Nyland         1
Álvaro Vadillo       1
Name: players, Length: 4018, dtype: int64

In [61]:
statsdf.loc[statsdf['players']=='Raúl García',['players','nationality','team','position','age','birth_year','index_year','stats_year']]

players nationality           team position   age  birth_year  \
6578  Raúl García      es ESP        Leganés       DF  28.0      1989.0   
6579  Raúl García      es ESP  Athletic Club    MF,FW  31.0      1986.0   
7362  Raúl García      es ESP  Athletic Club    MF,FW  32.0      1986.0   
7363  Raúl García      es ESP         Girona       DF  29.0      1989.0   
7364  Raúl García      es ESP        Leganés       DF  29.0      1989.0   
7927  Raúl García      es ESP  Athletic Club    MF,FW  33.0      1986.0   
7928  Raúl García      es ESP         Getafe       DF  30.0      1989.0   
7929  Raúl García      es ESP     Valladolid    DF,MF  30.0      1989.0   

      index_year stats_year  
6578        2018  2017-2018  
6579        2018  2017-2018  
7362        2019  2018-2019  
7363        2019  2018-2019  
7364        2019  2018-2019  
7927        2020  2019-2020  
7928        2020  2019-2020  
7929        2020  2019-2020

* Looking up Raul Garcia - there is the raul garcia that has been at Bilbao for years.
* The other 5 entries here are the same Raul Garcia.  He spent time on loan and therefore time at two clubs in 2019 and 2020.  
* Options:
    - combine the stats from the same year (all % columns will be unuseable)
    - Only use the stats for the selling club.  This is of course limited, but no more limited than not considering more than one season of work.

In [62]:
tfdf3['index_name'] = tfdf3['player']

In [63]:
statsdf['index_name'] = statsdf['players']

### nationality

In [64]:
tfdf3['nationality']

10      United States
38            England
39              Wales
57            England
65              Spain
            ...      
9232        Argentina
9320          Germany
9321         Cameroon
9455          Croatia
9466           Guinea
Name: nationality, Length: 1107, dtype: object

In [65]:
statsdf['nationality']

0       ar ARG
1       al ALB
2       de GER
3       br BRA
4       ch SUI
         ...  
8072    es ESP
8073    es ESP
8074    es ESP
8075    tr TUR
8076    hr CRO
Name: nationality, Length: 8076, dtype: object

Creating a dictionary of country abbreviations to create a new column in the stats df that is the full name of the nation to facilitate index matching with nationality in the transfer df

In [66]:
#from: https://www.realifewebdesigns.com/web-marketing/abbreviations-countries.asp
country_abb = pd.read_excel('data/country_abbreviations.xlsx', header=None)

In [67]:
#format: "AF = Afghanistan"
#extracting the country code abbreviation and country name as key and value for dictionary
country_abb['key'] = country_abb[0].apply(lambda x: x[0:2].lower())
country_abb['value'] = country_abb[0].apply(lambda x: x[4:])

In [68]:
#dropping original column
country_abb.drop(labels=0, axis=1, inplace=True)

In [69]:
#Convert series to lists to facilitate creation of dictionary
key_list = list(country_abb['key'])
value_list = list(country_abb['value'])

In [70]:
country_dict = {}
for n in range(len(key_list)):
    country_dict[key_list[n]] = value_list[n]

In [75]:
#Extracting the abbreviation from the nationality column (formatting as "ar ARG")
statsdf['nationality_abb'] = statsdf['nationality'].str.extract(r'([a-z]+)')

In [76]:
#the entries for guadelupe were missing the two letter code
#French guiana's code is GUF, the one GYF is a data entry error correcting here
#explains the nunique discrepancy 
statsdf.loc[statsdf['nationality'] == ' GPE', 'nationality_abb'] = 'gp' 
statsdf.loc[statsdf['nationality'] == ' GYF', 'nationality_abb'] = 'gf'

In [ ]:
# print(statsdf['nationality'].nunique())
# print(statsdf['nationality_abb'].nunique())

# print(statsdf['nationality'].value_counts())
# print(statsdf['nationality_abb'].value_counts())

In [77]:
#Manually entering missing abbreviations from the list from the website to faciliate recoding:
country_dict['cw'] = 'Curacao'
country_dict['eng'] = 'England'
country_dict['is'] = 'Iceland'
country_dict['rs'] = 'Serbia'
country_dict['xk'] = 'Kosovo'
country_dict['wal'] = 'Wales'
country_dict['sco'] = 'Scotland'
country_dict['nir'] = 'Northern Ireland'
country_dict['me'] = 'Montenegro'

In [78]:
statsdf['index_nationality'] = statsdf['nationality_abb'].map(lambda x: country_dict[x])

In [79]:
tfdf3['index_nationality'] = tfdf3['nationality']

## Indexing on selling club in transfer data and club in stats data

* The previous league column in tfdf3 is more correctly previous country.  Therefore includes purchases from lower leagues and academies not just top tier.  Therefore tfdf3 has more clubs than appear in the stats dataset.  The team in statsdf is the more generic version.  
* Import a dictionary with generic name as key and full name as value from pyfiles to add to the statsdf for index matching.

In [83]:
import py_files.team_dictionary as team_dict

In [84]:
team_dict = team_dict.team_dict

In [85]:
statsdf['index_selling_club'] = statsdf['team'].map(lambda x: team_dict[x])

In [86]:
tfdf3['index_selling_club'] = tfdf3['selling_club']

In [ ]:
# These were to be used for merging (see below)
# tfdf3.set_index(keys=['index_name','index_nationality','index_selling_club','index_year'], inplace=True)
# statsdf.set_index(keys=['index_name','index_nationality','index_selling_club','index_year'], inplace=True)

# Merging transfer and stats dataframes by index

## Original idea
* Merging on name, nationality, selling club and year (stats year lagged one behind sell year)
* Did not use age because the timing of the entry in either database was unclear so couldn't get a consistent number lagged or otherwise
## Problems with this approach
* There are players that are transferred multiple times in the same year
    - e.g.,  Omar Mascarell. Madrid exercised a buy back and then sold (one stats year, two transfers)
    - e.g., Marc Cucurella. Loaned to Eibar 2018/2019, option to make permanent in summer 2019.  Barca rebought 16 days later and loaned him to Getafe.  Permanently sold to Getafe summer 2020.
    * IMPACT: We might assume buybacks are set based on the performance prior to their loan but there is nothing in the dataset indicating options to buy (or release fees).  Treating these as independent transactions based on the same performance year.
* There are players in the stats with multiple observations per year:
    - Loans/January moves/extended window, e.g., Naldo, Adama Traoré, Rafinha - One full year of stats spread across multiple teams
    - Mulitple people with same name, nationality, e.g., Naldo which means we can't just sum by player and year
    - IMPACT: we can't match based on club because of the multi club problem and we can't sum by player and year because of the multi player problem.  
* Solution: merge by name and year 736 rows
    - When merging the transfers dataframe and stats dataframe using an inner merge we will only get those that appear in both so will keep all transfers that involve moves between teams in the big 5 leagues.  
    - There will be two kinds of dual labeling:
        - For different players with the same name
        - For players that played for multiple clubs in one year
        - ID manually

In [92]:
df = tfdf3.merge(statsdf, on=['index_name','index_year'])

In [93]:
df.shape

(736, 141)

In [94]:
pd.options.display.max_rows = 736
df

player  age_x             nationality_x  \
0         Christian Pulisic     20             United States   
1           Dominic Solanke     21                   England   
2             Emiliano Sala     28                 Argentina   
3              Riyad Mahrez     27                   Algeria   
4                 Lee Grant     35                   England   
5                   Alisson     25                    Brazil   
6                Naby Keïta     23                    Guinea   
7                   Fabinho     24                    Brazil   
8           Xherdan Shaqiri     26               Switzerland   
9                  Jorginho     26                     Italy   
10           Lucas Torreira     22                   Uruguay   
11               Bernd Leno     26                   Germany   
12                 Joe Hart     31                   England   
13              Richarlison     21                    Brazil   
14               Yerry Mina     23                  Colombia   
15              Lucas Digne     25                    France   
16           Rachid Ghezzal     26                   Algeria   
17              Jonny Evans     30          Northern Ireland   
18             Mikel Merino     22                     Spain   
19             Mikel Merino     22                     Spain   
20       Federico Fernández     29                 Argentina   
21             Fabian Schär     26               Switzerland   
22         Cheikhou Kouyaté     28                   Senegal   
23          Jefferson Lerma     23                  Colombia   
24               Diego Rico     25                     Spain   
25          Felipe Anderson     25                    Brazil   
26                Issa Diop     21                    France   
27        Andriy Yarmolenko     28                   Ukraine   
28              Lucas Pérez     29                     Spain   
29          Gerard Deulofeu     24                     Spain   
30          Gerard Deulofeu     24                     Spain   
31              Adam Masina     24                     Italy   
32               Ben Foster     35                   England   
33             Marc Navarro     22                     Spain   
34            Yves Bissouma     21                      Mali   
35                 Bernardo     23                    Brazil   
36           Martín Montoya     27                     Spain   
37            Florin Andone     25                   Romania   
38          Terence Kongolo     24               Netherlands   
39          Terence Kongolo     24               Netherlands   
40           Adama Diakhaby     22                    France   
41            Ramadan Sobhi     21                     Egypt   
42      Florent Hadergjonaj     23                    Kosovo   
43              Jonas Lössl     29                   Denmark   
44       Jannik Vestergaard     25                   Denmark   
45             Adama Traoré     22                     Spain   
46              Benik Afobe     25                  DR Congo   
47            João Moutinho     31                  Portugal   
48             Alfie Mawson     24                   England   
49       Maxime Le Marchand     28                    France   
50         Ignacio Pussetto     24                 Argentina   
51               Aaron Mooy     29                 Australia   
52               Lukas Rupp     29                   Germany   
53             João Cancelo     25                  Portugal   
54                    Rodri     23                     Spain   
55              Pedro Porro     19                     Spain   
56           Ryan Sessegnon     19                   England   
57             Nicolas Pépé     24             Cote d'Ivoire   
58           William Saliba     18                    France   
59               David Luiz     32                    Brazil   
60            Harry Maguire     26                   England   
61        Aaron Wan-Bissaka     21                   

In [97]:
df['player'].value_counts()

João Cancelo              3
Leandro Cabrera           3
Leonardo Bittencourt      3
Enric Gallego             3
Vincent Pajot             3
Giovani Lo Celso          3
Marc Cucurella            3
Vincenzo Grifo            3
Karl Toko Ekambi          3
Jeison Murillo            3
Alfred Gomis              3
Rémy Cabella              3
Marius Wolf               2
Jeff Reine-Adélaïde       2
Kevin-Prince Boateng      2
Lukas Lerager             2
Kyle Walker-Peters        2
Jordan Ferri              2
Emil Krafth               2
Martin Braithwaite        2
Gabriel                   2
Davy Klaassen             2
Yannis Salibur            2
Emre Can                  2
Lucas Pérez               2
Luis Muriel               2
Khouma Babacar            2
Loïc Rémy                 2
Youssef En-Nesyri         2
Ryad Boudebouz            2
Alfred Duncan             2
Marco Tumminello          2
Diego Falcinelli          2
Christian Kouamé          2
Andrea Petagna            2
Vincent Laurini     

In [201]:
df.loc[df['player']=="Terence Kongolo"]

player  age_x nationality_x   position_x selling_club  \
38  Terence Kongolo     24   Netherlands  Centre-Back    AS Monaco   
39  Terence Kongolo     24   Netherlands  Centre-Back    AS Monaco   

   previous_league est_market_value      fee        buying_club window  \
38          France           £9.00m  £18.00m  Huddersfield Town  s_w=s   
39          France           £9.00m  £18.00m  Huddersfield Town  s_w=s   

    transfer_year buying_league  loan  free  buying_top_5 currency multiplier  \
38           2018           GB1     0     0             1        £          m   
39           2018           GB1     0     0             1        £          m   

    fee_numerical   mult_num   fee_final  index_year       index_name  \
38           18.0  1000000.0  18000000.0        2018  Terence Kongolo   
39           18.0  1000000.0  18000000.0        2018  Terence Kongolo   

   index_nationality_x index_selling_club_x          players nationality_y  \
38         Netherlands            AS Monaco  Terence Kongolo        nl NED   
39         Netherlands            AS Monaco  Terence Kongolo        nl NED   

            team position_y  age_y  birth_year  games  games_start   mins  \
38  Huddersfield         DF   23.0      1994.0     13           11  1,049   
39        Monaco         DF   23.0      1994.0      3            3    256   

    goals  assists  pens_successful  pens_attempts  yellow_cards  red_cards  \
38      0        0                0              0             0          0   
39      0        0                0              0             0          0   

    goals_per_90  assists_per_90  goals_and_assists_per_90  goals_pk_per_90  \
38           0.0             0.0                       0.0              0.0   
39           0.0             0.0                       0.0              0.0   

    goals_assists_pk_per_90   xg  npxp   xa  xg_per90  xa_per90  \
38                      0.0  0.3   0.3  0.3      0.02      0.03   
39                      0.0  0.1   0.1  0.3      0.04      0.12   

    xg_xa_per90_list  npxg_per90_list  npxg_xa_per90  full_90s_played  \
38              0.05             0.02           0.05             11.7   
39              0.16             0.04           0.16              2.8   

    shots_total  shots_on_target  shots_total_per90  shots_on_target_per90  \
38          2.0                0               0.17                    0.0   
39          1.0                0               0.35                    0.0   

    npxg  ...  sca_defense  gca  gca_per90  gca_passes_live  gca_passes_dead  \
38   0.3  ...          0.0  1.0       0.09              1.0              0.0   
39   0.1  ...          0.0  1.0       0.35              1.0              0.0   

    gca_dribbles  gca_shots  gca_fouled  gca_defense  gca_og_for  tackles  \
38           0.0        0.0         0.0          0.0         0.0     32.0   
39           0.0        0.0         0.0          0.0         0.0      6.0   

    tackles_won  tackles_def_3rd  tackles_mid_3rd  tackles_att_3rd  \
38         15.0             16.0             15.0              1.0   
39          5.0              5.0              1.0              0.0   

    dribble_tackles  dribble_vs  dribbled_past  pressures  pressure_regains  \
38              8.0        17.0            9.0      144.0              46.0   
39              3.0         5.0            2.0       24.0               4.0   

    pressures_def_3rd  pressures_mid_3rd  pressures_att_3rd  blocks  \
38               94.0               39.0               11.0    26.0   
39               11.0                8.0                5.0     6.0   

    blocked_shots  blocked_shots_saves  blocked_passes  interceptions  \
38            8.0                  0.0            18.0           20.0   
39            3.0                  0.0             3.0            3.0   

    tackles_interceptions  clearances  errors  touches  touches_def_pen_area  \
38                     52        41.0     1.0    540.0                  56.0   

Time at multiple clubs one year:
Terence Kongolo 2018 38/39
Enzo Crivelli 2018 131/132
Clément Grenier 2018 161/162
Alessandro Murgia 2019 645/646
Youri Tielemans 2019 70/71
Nenad Tomović 2018 514/515
André Silva 2020 490/491
Suso 2020 387/388
Marco Capuano 2018 525/526 
Gelson Martins 2019 191/192
Carles Pérez 2020 692/693
Koffi Djidji 2019 652/653
Rúben Vezo 2019 368/369
Facundo Roncaglia 2019 377/378
Roberto Soriano 2019 592/593
Luca Pellegrini 2019 614/615
Souleyman Doumbia 2020 242/243
Sebastien De Maio 2019 656/657
Coke 2018 287/288
Gonçalo Guedes 2018 306/307
Valon Berisha 2020 232/233
Giuseppe Pezzella 2020 687/688
Yassine Benrahou 2020 253/254
Soualiho Meïté 2018 569/570
Martin Hinteregger 2019 458/459
Dawid Kownacki 2019 438/439
Nicola Sansone 2019 590/591
Roque Mesa 2018 303/304
Kylian Mbappé 2018 156/157
John Guidetti 2018 274/275
Takashi Inui 2019 355/356
Fabrizio Cacciatore 2019 598/599
Pablo Hervías 2019 372/373
Gerard Deulofeu 2018 29/30
Vid Belec 2018 556/557
Ondrej Duda 2020 496/497
Denis Suárez 2019 374/375
Dimitri Foulquier 2020 394/395
Sergi Darder 2018 289/290
Christian Kouamé 2020 673/674
Diego Falcinelli 2018 509/510
Marco Tumminello 2018 506/507
Alfred Duncan 2020 670/671
Ryad Boudebouz 2019 212/213
Joao Cancelo 2018 (index 533 for inter, index 534 1 game for Valencia)
Leandro Cabrera 2018 spent time at (index 283, 284) Crotone and Getafe 
Leonardo Bittencourt 2020 (499 and 5000 time at two clubs
Enric Gallego 2020 (396 397)
Vincent Pajot 2020 250/251 time at two clubs
Giovani Lo Celso 2019 360/361
Vincenzo Grifo 2019 471/472
Karl Toko Ekambi 2020 236/237
Jeison Murillo 2019 584/585
Rémy Cabella 2018 164/165
Kevin-Prince Boateng 2019 601/602
Lukas Lerager 2019 607/608
Kyle Walker-Peters 2020 117/118
Jordan Ferri 2019 198/199
Yannis Salibur 2019 380/381
Emre Can 2020 484/485
Luis Muriel 2019 587/588
Khouma Babacar 2018 558/559
Loïc Rémy 2018 139/140

Purchased multiple times same year:
Ionuț Radu 2019
Mikel Merino purchased twice summer 2018
Marc Cucurella 2019
Marius Wolf 2018
Emil Krafth 2019
Martin Braithwaite 2019
Andrea Petagna 2019
Andrea Pinamonti 2020
Omar Mascarell 2018
Paco Alcácer 2019

Danilo index 595 has man city danilo's statistics 
Danilo index 596 is correct
Naldo index 127 delete
Gabriel to Arsenal 2020 (index 95) stats are wrong
Gabriel to Benfica 2018 index 708 are correct